In [1]:
import tensorflow as tf


C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:519: FutureWarning: Passi

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from tensorflow.examples.tutorials.mnist import input_data
import time
%matplotlib inline
import os
import uff

In [3]:
data = input_data.read_data_sets('data/fashion',one_hot=True,\
                                 source_url='http://fashion-mnist.s3-website.eu-central-1.amazonaws.com/')

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting data/fashion\train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting data/fashion\train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Extracting data/fashion\t10k-images-idx3-ubyte.gz
Extracting data/fashion\t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.


In [20]:
train_X = data.train.images.reshape(-1, 28, 28, 1)
test_X = data.test.images.reshape(-1,28,28,1)
train_y = data.train.labels
test_y = data.test.labels
training_iters = 10
learning_rate = 0.001
batch_size = 128

# MNIST data input (img shape: 28*28)
n_input = 28

# MNIST total classes (0-9 digits)
n_classes = 10

In [5]:
x = tf.placeholder("float", [None, 28,28,1])
y = tf.placeholder("float", [None, n_classes])

In [6]:
def conv2d(x, W, b, strides=1):
    # Conv2D wrapper, with bias and relu activation
    x = tf.nn.conv2d(x, W, strides=[1, strides, strides, 1], padding='SAME')
    x = tf.nn.bias_add(x, b)
    return tf.nn.relu(x)

def maxpool2d(x, k=2):
    return tf.nn.max_pool(x, ksize=[1, k, k, 1], strides=[1, k, k, 1],padding='SAME')

In [8]:
weights = {
    'wc1': tf.get_variable('W0', shape=(3,3,1,32), initializer=tf.contrib.layers.xavier_initializer()),
    'wc2': tf.get_variable('W1', shape=(3,3,32,64), initializer=tf.contrib.layers.xavier_initializer()),
    'wc3': tf.get_variable('W2', shape=(3,3,64,128), initializer=tf.contrib.layers.xavier_initializer()),
    'wd1': tf.get_variable('W3', shape=(4*4*128,128), initializer=tf.contrib.layers.xavier_initializer()),
    'out': tf.get_variable('W6', shape=(128,n_classes), initializer=tf.contrib.layers.xavier_initializer()),
}
biases = {
    'bc1': tf.get_variable('B0', shape=(32), initializer=tf.contrib.layers.xavier_initializer()),
    'bc2': tf.get_variable('B1', shape=(64), initializer=tf.contrib.layers.xavier_initializer()),
    'bc3': tf.get_variable('B2', shape=(128), initializer=tf.contrib.layers.xavier_initializer()),
    'bd1': tf.get_variable('B3', shape=(128), initializer=tf.contrib.layers.xavier_initializer()),
    'out': tf.get_variable('B4', shape=(10), initializer=tf.contrib.layers.xavier_initializer()),
}

def conv_net(x, weights, biases):  

    # here we call the conv2d function we had defined above and pass the input image x, weights wc1 and bias bc1.
    conv1 = conv2d(x, weights['wc1'], biases['bc1'])
    # Max Pooling (down-sampling), this chooses the max value from a 2*2 matrix window and outputs a 14*14 matrix.
    conv1 = maxpool2d(conv1, k=2)

    # Convolution Layer
    # here we call the conv2d function we had defined above and pass the input image x, weights wc2 and bias bc2.
    conv2 = conv2d(conv1, weights['wc2'], biases['bc2'])
    # Max Pooling (down-sampling), this chooses the max value from a 2*2 matrix window and outputs a 7*7 matrix.
    conv2 = maxpool2d(conv2, k=2)

    conv3 = conv2d(conv2, weights['wc3'], biases['bc3'])
    # Max Pooling (down-sampling), this chooses the max value from a 2*2 matrix window and outputs a 4*4.
    conv3 = maxpool2d(conv3, k=2)


    # Fully connected layer
    # Reshape conv2 output to fit fully connected layer input
    fc1 = tf.reshape(conv3, [-1, weights['wd1'].get_shape().as_list()[0]])
    fc1 = tf.add(tf.matmul(fc1, weights['wd1']), biases['bd1'])
    fc1 = tf.nn.relu(fc1)
    # Output, class prediction
    # finally we multiply the fully connected layer with the weights and add a bias term.
    out = tf.add(tf.matmul(fc1, weights['out']), biases['out'], name='output')
    return out

In [9]:
pred = conv_net(x, weights, biases)
cost = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits=pred, labels=y))
optimizer = tf.train.AdamOptimizer(learning_rate=learning_rate).minimize(cost)

correct_prediction = tf.equal(tf.argmax(pred, 1), tf.argmax(y, 1))
#calculate accuracy across all the given images and average them out.
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))
init = tf.global_variables_initializer()
saver = tf.train.Saver()

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [23]:
with tf.Session() as sess:
    sess.run(init)
    train_loss = []
    test_loss = []
    train_accuracy = []
    test_accuracy = []
    summary_writer = tf.summary.FileWriter('./Output', sess.graph)
    for i in range(training_iters):
        for batch in range(len(train_X)//batch_size):
            batch_x = train_X[batch*batch_size:min((batch+1)*batch_size,len(train_X))]
            batch_y = train_y[batch*batch_size:min((batch+1)*batch_size,len(train_y))]    
            # Run optimization op (backprop).
                # Calculate batch loss and accuracy
            opt = sess.run(optimizer, feed_dict={x: batch_x,
                                                              y: batch_y})
            
            loss, acc = sess.run([cost, accuracy], feed_dict={x: batch_x,
                                                              y: batch_y})
        print("Iter " + str(i) + ", Loss= " + \
                      "{:.6f}".format(loss) + ", Training Accuracy= " + \
                      "{:.5f}".format(acc))
        print("Optimization Finished!")

        # Calculate accuracy for all 10000 mnist test images
        
        
        train_loss.append(loss)
        train_accuracy.append(acc)
        
        
    start = time.process_time()
    test_acc,valid_loss = sess.run([accuracy,cost], feed_dict={x: test_X,y : test_y})
    print('\n\n\n\n\n\n')
    print('The time required for predicting Test Dataset images is '+str(time.process_time()-start)+' s ')
    test_loss.append(valid_loss)
    test_accuracy.append(test_acc)
    print("Testing Accuracy:","{:.5f}".format(test_acc))
    saver.save(sess, 'C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/model_tf.chkp')
    tf.train.write_graph(sess.graph_def,'uu/', 'save_tf_model.pbtxt')
    summary_writer.close()

Iter 0, Loss= 0.373038, Training Accuracy= 0.85938
Optimization Finished!
Iter 1, Loss= 0.255477, Training Accuracy= 0.89844
Optimization Finished!
Iter 2, Loss= 0.174895, Training Accuracy= 0.93750
Optimization Finished!
Iter 3, Loss= 0.150188, Training Accuracy= 0.96094
Optimization Finished!
Iter 4, Loss= 0.154912, Training Accuracy= 0.94531
Optimization Finished!
Iter 5, Loss= 0.141375, Training Accuracy= 0.94531
Optimization Finished!
Iter 6, Loss= 0.129541, Training Accuracy= 0.94531
Optimization Finished!
Iter 7, Loss= 0.120134, Training Accuracy= 0.95312
Optimization Finished!
Iter 8, Loss= 0.110043, Training Accuracy= 0.94531
Optimization Finished!
Iter 9, Loss= 0.116910, Training Accuracy= 0.94531
Optimization Finished!







The time required for predicting Test Dataset images is 10.4375 s 
Testing Accuracy: 0.90210


In [15]:
import numpy as np
from tensorflow.python.tools import freeze_graph

In [16]:
# Freeze the graph
save_path="C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/" #directory to model files
MODEL_NAME = 'tf_model' #name of the model optional
input_graph_path = save_path+'save_tf_model.pbtxt'#complete path to the input graph
checkpoint_path = save_path+'model_tf.chkp' #complete path to the model's checkpoint file
input_saver_def_path = ""
input_binary = False
output_node_names = "output" #output node's name. Should match to that mentioned in your code
restore_op_name = "save/restore_all"
filename_tensor_name = "save/Const:0"
output_frozen_graph_name = save_path+'frozen_'+MODEL_NAME+'.pb' # the name of .pb file you would like to give
clear_devices = True

In [18]:
freeze_graph.freeze_graph(input_graph_path, input_saver_def_path,
                          input_binary, checkpoint_path, output_node_names,
                          restore_op_name, filename_tensor_name,
                          output_frozen_graph_name, clear_devices, "")

INFO:tensorflow:Restoring parameters from C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/model_tf.chkp
INFO:tensorflow:Froze 10 variables.
INFO:tensorflow:Converted 10 variables to const ops.


node {
  name: "Placeholder"
  op: "Placeholder"
  attr {
    key: "dtype"
    value {
      type: DT_FLOAT
    }
  }
  attr {
    key: "shape"
    value {
      shape {
        dim {
          size: -1
        }
        dim {
          size: 28
        }
        dim {
          size: 28
        }
        dim {
          size: 1
        }
      }
    }
  }
}
node {
  name: "W0"
  op: "Const"
  attr {
    key: "dtype"
    value {
      type: DT_FLOAT
    }
  }
  attr {
    key: "value"
    value {
      tensor {
        dtype: DT_FLOAT
        tensor_shape {
          dim {
            size: 3
          }
          dim {
            size: 3
          }
          dim {
            size: 1
          }
          dim {
            size: 32
          }
        }
        tensor_content: "\224\3238\276\357\323M>5\216%>a\367\232<\333\321H>\207\246\001\2754M\326=)\277\005>\002\346\346\275\370Z\202\274J\014h\275|.r=\232V\347=\221\363M=\343\3446>.\273.\276\305h\345=d\017\275=\330{\037\275\177\3137

In [19]:
uff.from_tensorflow(graphdef='C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/frozen_tf_model.pb',
                    output_filename='C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/uff_model_tf.uff',
                    text=True)



UFF Version 0.6.5
=== Automatically deduced input nodes ===
[name: "Placeholder"
op: "Placeholder"
attr {
  key: "dtype"
  value {
    type: DT_FLOAT
  }
}
attr {
  key: "shape"
  value {
    shape {
      dim {
        size: -1
      }
      dim {
        size: 28
      }
      dim {
        size: 28
      }
      dim {
        size: 1
      }
    }
  }
}
]

=== Automatically deduced output nodes ===
[name: "output"
op: "Add"
input: "MatMul_1"
input: "B4/read"
attr {
  key: "T"
  value {
    type: DT_FLOAT
  }
}
]

Using output node output
Converting to UFF graph
DEBUG [C:\ProgramData\Anaconda3\lib\site-packages\uff\converters\tensorflow\converter.py:96] Marking ['output'] as outputs
No. nodes: 31
UFF Output written to C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/uff_model_tf.uff
UFF Text Output written to C:/Users/PRATHAMESH/Deep_Learning/Adagrad/uu/uff_model_tf.pbtxt


b'\x08\x01\x10\x01\x1a\x18\n\x14tensorflow_extension\x10\x01"\xb4\x12\n\x04main\x12-\n\x06output\x12\x08MatMul_1\x12\x02B4\x1a\x06Binary"\r\n\x04func\x12\x05\n\x03add\x12D\n\x02B4\x1a\x05Const"\x0e\n\x05shape\x12\x05B\x03\n\x01\n"\x17\n\x06values\x12\r\xa2\x06\nweights_B4"\x0e\n\x05dtype\x12\x05\xa8\x06\xa0\x80\x08\x12H\n\x08MatMul_1\x12\x06Relu_3\x12\x02W6\x1a\x0eFullyConnected" \n\rinputs_orders\x12\x0f\xa2\x06\x0corders_NC_CK\x12F\n\x02W6\x1a\x05Const"\x10\n\x05shape\x12\x07B\x05\n\x03\x80\x01\n"\x17\n\x06values\x12\r\xa2\x06\nweights_W6"\x0e\n\x05dtype\x12\x05\xa8\x06\xa0\x80\x08\x12)\n\x06Relu_3\x12\x03Add\x1a\nActivation"\x0e\n\x04func\x12\x06\n\x04relu\x12(\n\x03Add\x12\x06MatMul\x12\x02B3\x1a\x06Binary"\r\n\x04func\x12\x05\n\x03add\x12E\n\x02B3\x1a\x05Const"\x0f\n\x05shape\x12\x06B\x04\n\x02\x80\x01"\x17\n\x06values\x12\r\xa2\x06\nweights_B3"\x0e\n\x05dtype\x12\x05\xa8\x06\xa0\x80\x08\x12G\n\x06MatMul\x12\x07Reshape\x12\x02W3\x1a\x0eFullyConnected" \n\rinputs_orders\x12\x0f\xa2